# Your Title Here

**Name(s)**: Brandon Chu
**Website Link**: (your website link)

In [2]:
import pandas as pd
import numpy as np
from pathlib import Path

import plotly.express as px
pd.options.plotting.backend = 'plotly'

from dsc80_utils import * # Feel free to uncomment and use this.

In [3]:
lol = pd.read_csv('lol.csv')
lol

c:\Users\brand\miniforge3\envs\dsc80\lib\site-packages\IPython\core\interactiveshell.py:3508: DtypeWarning:

Columns (2) have mixed types.Specify dtype option on import or set low_memory=False.



gameid datacompleteness  \
0       ESPORTSTMNT01_2690210         complete   
1       ESPORTSTMNT01_2690210         complete   
2       ESPORTSTMNT01_2690210         complete   
...                       ...              ...   
148989       9687-9687_game_5          partial   
148990       9687-9687_game_5          partial   
148991       9687-9687_game_5          partial   

                                                url league  ...  deathsat15  \
0                                               NaN   LCKC  ...         0.0   
1                                               NaN   LCKC  ...         2.0   
2                                               NaN   LCKC  ...         0.0   
...                                             ...    ...  ...         ...   
148989  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  ...         NaN   
148990  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  ...         NaN   
148991  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  ...         NaN   

       opp_killsat15  opp_assistsat15 opp_deathsat15  
0                0.0              1.0            0.0  
1                0.0              5.0            1.0  
2                3.0              3.0            2.0  
...              ...              ...            ...  
148989           NaN              NaN            NaN  
148990           NaN              NaN            NaN  
148991           NaN              NaN            NaN  

[148992 rows x 131 columns]

## Step 1: Introduction

**How do ban patterns vary by region and how do they affect win percentage?**

Do teams favor a dragon soul and how does it affect win percentage?

Do position-focused bans(banning out a position) work out better than spread-out bans?

How has game length changed over the patches?






## Step 2: Data Cleaning and Exploratory Data Analysis

IMPORTANT: dropped: graves, maokai, seraphine, sett

because less than 60% were picked for their main role

In [4]:
lol_sub = lol[['gameid', 'side', 'ban1', 'ban2', 'ban3', 'ban4', 'ban5','pick1', 'pick2', 'pick3', 'pick4', 'pick5', 'league', 'patch', 'result']]



position_mappings = {
    'Aatrox': 'top', 'Ahri': 'mid', 'Akali': 'mid', 'Akshan': 'top', 'Alistar': 'sup', 'Amumu': 'sup', 'Anivia': 'mid',
    'Annie': 'mid', 'Aphelios': 'adc', 'Ashe': 'adc', 'Aurelion Sol': 'mid', 'Azir': 'mid', 'Bard': 'sup', "Bel'Veth": 'jg',
    'Blitzcrank': 'sup', 'Brand': 'sup', 'Braum': 'sup', 'Briar': 'jg', 'Caitlyn': 'adc', 'Camille': 'top', 'Cassiopeia': 'mid',
    "Cho'Gath": 'top', 'Corki': 'mid', 'Darius': 'top', 'Diana': 'jg', 'Draven': 'adc', 'Dr. Mundo': 'top', 'Ekko': 'mid',
    'Elise': 'jg', 'Evelynn': 'jg', 'Ezreal': 'adc', 'Fiddlesticks': 'jg', 'Fiora': 'top', 'Fizz': 'mid', 'Galio': 'mid',
    'Gangplank': 'top', 'Garen': 'top', 'Gnar': 'top', 'Gragas': 'jg', 'Graves': '', 'Gwen': 'top', 'Hecarim': 'jg',
    'Heimerdinger': 'mid', 'Hwei': 'mid', 'Illaoi': 'top', 'Irelia': 'top', 'Ivern': 'jg', 'Janna': 'sup', 'Jarvan IV': 'jg',
    'Jax': 'top', 'Jayce': 'top', 'Jhin': 'adc', 'Jinx': 'adc', "Kai'Sa": 'adc', 'Kalista': 'adc', 'Karma': 'sup', 'Karthus': 'jg',
    'Kassadin': 'mid', 'Katarina': 'mid', 'Kayle': 'top', 'Kayn': 'jg', 'Kennen': 'top', "Kha'Zix": 'jg', 'Kindred': 'jg',
    'Kled': 'top', "Kog'Maw": 'adc', "K'Sante": 'top', 'LeBlanc': 'mid', 'Lee Sin': 'top', 'Leona': 'sup', 'Lillia': 'jg',
    'Lissandra': 'mid', 'Lucian': 'adc', 'Lulu': 'sup', 'Lux': 'mid', 'Malphite': 'top', 'Malzahar': 'mid', 'Maokai': '',
    'Master Yi': 'jg', 'Milio': 'sup', 'Miss Fortune': 'adc', 'Mordekaiser': 'top', 'Morgana': 'sup', 'Naafiri': 'mid',
    'Nami': 'sup', 'Nasus': 'top', 'Nautilus': 'sup', 'Neeko': 'mid', 'Nidalee': 'jg', 'Nilah': 'adc', 'Nocturne': 'jg',
    'Nunu & Willump': 'jg', 'Olaf': 'top', 'Orianna': 'mid', 'Ornn': 'top', 'Pantheon': 'jg', 'Poppy': 'jg', 'Pyke': 'sup',
    'Qiyana': 'jg', 'Quinn': 'top', 'Rakan': 'sup', 'Rammus': 'jg', "Rek'Sai": 'jg', 'Rell': 'sup', 'Renata Glasc': 'sup',
    'Renekton': 'top', 'Rengar': 'jg', 'Riven': 'top', 'Rumble': 'top', 'Ryze': 'mid', 'Samira': 'adc', 'Sejuani': 'jg', 'Seraphine': '', 'Sett': '', 
    'Senna': 'adc', 'Shaco': 'jg', 'Shen': 'top', 'Shyvana': 'top', 'Singed': 'top', 'Sion': 'top',
    'Sivir': 'adc', 'Skarner': 'jg', 'Smolder': 'adc', 'Sona': 'sup', 'Soraka': 'sup', 'Swain': 'mid', 'Sylas': 'mid', 'Syndra': 'mid',
    'Tahm Kench': 'sup', 'Taliyah': 'mid', 'Talon': 'jg', 'Taric': 'sup', 'Teemo': 'top', 'Thresh': 'sup', 'Tristana': 'adc',
    'Trundle': 'jg', 'Tryndamere': 'top', 'Twisted Fate': 'mid', 'Twitch': 'adc', 'Udyr': 'jg', 'Urgot': 'top', 'Varus': 'adc',
    'Vayne': 'adc', 'Veigar': 'mid', "Vel'Koz": 'mid', 'Vex': 'mid', 'Vi': 'jg', 'Viego': 'jg', 'Viktor': 'mid', 'Vladimir': 'mid',
    'Volibear': 'jg', 'Warwick': 'top', 'Wukong': 'jg', 'Xayah': 'adc', 'Xerath': 'mid', 'Xin Zhao': 'adc', 'Yasuo': 'mid',
    'Yone': 'mid', 'Yorick': 'top', 'Yuumi': 'sup', 'Zac': 'jg', 'Zed': 'mid', 'Zeri': 'adc', 'Ziggs': 'adc', 'Zilean': 'sup',
    'Zoe': 'mid', 'Zyra': 'sup'
}





In [5]:
lol_sub['ban1_pos'] = lol_sub['ban1'].map(position_mappings)
lol_sub['ban2_pos'] = lol_sub['ban2'].map(position_mappings)
lol_sub['ban3_pos'] = lol_sub['ban3'].map(position_mappings)
lol_sub['ban4_pos'] = lol_sub['ban4'].map(position_mappings)
lol_sub['ban5_pos'] = lol_sub['ban5'].map(position_mappings)


lol_sub['pick1_pos'] = lol_sub['pick1'].map(position_mappings)
lol_sub['pick2_pos'] = lol_sub['pick2'].map(position_mappings)
lol_sub['pick3_pos'] = lol_sub['pick3'].map(position_mappings)
lol_sub['pick4_pos'] = lol_sub['pick4'].map(position_mappings)
lol_sub['pick5_pos'] = lol_sub['pick5'].map(position_mappings)


In [6]:
ban_df = lol_sub.dropna(subset = ['ban1', 'ban2', 'ban3', 'ban4', 'ban5'], inplace=False)
ban_df = ban_df.groupby(['gameid', 'side']).agg(pd.Series.mode).reset_index()

In [7]:
ban_columns = ['ban1_pos', 'ban2_pos', 'ban3_pos', 'ban4_pos', 'ban5_pos']
position_columns = ['top', 'jg', 'adc', 'mid', 'sup']

ban_counts = ban_df[ban_columns].apply(lambda x: x.value_counts(), axis=1).fillna(0)

ban_counts['result'] = ban_df['result']

average_bans_by_result = ban_counts.groupby('result')[position_columns].mean()

average_bans_by_result

top        jg       adc       mid       sup
result                                                  
0       1.085124  0.741736  1.058099  1.250579  0.720248
1       1.052280  0.801930  1.015668  1.241115  0.733817

In [7]:
pick_df = lol_sub.copy()
pick_df = pick_df.groupby(['gameid', 'side']).agg(pd.Series.mode).reset_index()

pick_df['pick1'] = pick_df['pick1'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)
pick_df['pick2'] = pick_df['pick2'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)
pick_df['pick3'] = pick_df['pick3'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)
pick_df['pick4'] = pick_df['pick4'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)
pick_df['pick5'] = pick_df['pick5'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)

pick_df['ban1'] = pick_df['ban1'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)
pick_df['ban2'] = pick_df['ban2'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)
pick_df['ban3'] = pick_df['ban3'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)
pick_df['ban4'] = pick_df['ban4'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)
pick_df['ban5'] = pick_df['ban5'].apply(lambda x: np.NaN if isinstance(x, np.ndarray) else x)



pick_df.dropna(subset = ['pick1', 'pick2', 'pick3', 'pick4', 'pick5'], inplace=True)

In [5]:
position_pick_order_df = pd.DataFrame()
for i in range(1, 6):
    temp_df = pick_df[pick_df[f'pick{i}_pos'].notnull()]
    temp_df = temp_df[[f'pick{i}_pos']].rename(columns={f'pick{i}_pos': 'position'})
    temp_df['pick_order'] = i  
    position_pick_order_df = pd.concat([position_pick_order_df, temp_df])

average_pick_order = position_pick_order_df.groupby('position')['pick_order'].mean().reset_index()

average_pick_order = average_pick_order.sort_values(by='pick_order')

average_pick_order = average_pick_order.drop(0, axis = 'index')



KeyError: 'pick1_pos'

In [8]:
fig = px.bar(average_pick_order, x='position', y='pick_order',
             title='Average Pick Order by Position',
             labels={'pick_order': 'Average Pick Order', 'position': 'Position'},
             text='pick_order')
fig.update_layout(xaxis_title='Position',
                  yaxis_title='Average Pick Order',
                  yaxis=dict(tickmode='array', tickvals=[1, 2, 3, 4, 5]),
                  plot_bgcolor='white')

fig.show()


NameError: name 'average_pick_order' is not defined

In [ ]:
pick_df_won = pick_df[pick_df['result'] == 1]
pick_df_lost = pick_df[pick_df['result'] == 0]


won_pick_order_df = pd.DataFrame()
for i in range(1, 6):
    temp = pick_df_won[pick_df_won[f'pick{i}_pos'].notnull()]
    temp = temp[[f'pick{i}_pos']].rename(columns={f'pick{i}_pos': 'position'})
    temp['pick_order'] = i  
    won_pick_order_df = pd.concat([won_pick_order_df, temp])
    won_pick_order_df['result'] = 'won'


lost_pick_order_df = pd.DataFrame()
for i in range(1, 6):
    temp = pick_df_lost[pick_df_lost[f'pick{i}_pos'].notnull()]
    temp = temp[[f'pick{i}_pos']].rename(columns={f'pick{i}_pos': 'position'})
    temp['pick_order'] = i  
    lost_pick_order_df = pd.concat([lost_pick_order_df, temp])
    lost_pick_order_df['result'] = 'lost'



all_pick_order_df = pd.concat([lost_pick_order_df, won_pick_order_df], ignore_index = True)
all_pick_order_df = all_pick_order_df[all_pick_order_df['position'] != '']

fig = px.box(all_pick_order_df, x = 'position', y = 'pick_order', 
            color = 'result', title = 'Pick Order by Position For Winning Versus Losing Teams', labels = {'position': 'Position', 'pick_order': 'Pick Order'}
            )

fig.update_layout(xaxis_title='Position',
                  yaxis_title='Pick Order',
                  plot_bgcolor='white'
                  )
fig.update_xaxes(categoryarray= ['top', 'jg', 'mid', 'adc', 'sup'])

fig.show()


In [47]:
pick_df_won = pick_df[pick_df['result'] == 1]
pick_df_lost = pick_df[pick_df['result'] == 0]


won_pick_order_df = pd.DataFrame()
for i in range(1, 6):
    temp = pick_df_won[pick_df_won[f'pick{i}_pos'].notnull()]
    temp = temp[[f'pick{i}_pos']].rename(columns={f'pick{i}_pos': 'position'})
    temp['pick_order'] = i  
    won_pick_order_df = pd.concat([won_pick_order_df, temp])
    won_pick_order_df['result'] = 'won'


lost_pick_order_df = pd.DataFrame()
for i in range(1, 6):
    temp = pick_df_lost[pick_df_lost[f'pick{i}_pos'].notnull()]
    temp = temp[[f'pick{i}_pos']].rename(columns={f'pick{i}_pos': 'position'})
    temp['pick_order'] = i  
    lost_pick_order_df = pd.concat([lost_pick_order_df, temp])
    lost_pick_order_df['result'] = 'lost'



all_pick_order_df = pd.concat([lost_pick_order_df, won_pick_order_df], ignore_index = True)
all_pick_order_df = all_pick_order_df[all_pick_order_df['position'] != '']

fig = px.box(all_pick_order_df, x = 'position', y = 'pick_order', 
            color = 'result', title = 'Pick Order by Position For Winning Versus Losing Teams', labels = {'position': 'Position', 'pick_order': 'Pick Order'}
            )

fig.update_layout(xaxis_title='Position',
                  yaxis_title='Pick Order',
                  plot_bgcolor='white'
                  )

fig.update_xaxes(categoryarray= ['top', 'jg', 'mid', 'adc', 'sup'])


fig.show()


IDEAS: r5 renekton for hypothesis testing

## Step 3: Assessment of Missingness

## NMAR Analysis

I don't believe that any columns in this dataset are truly Not Missing at Random(NMAR). The data has many columns with non-trivial missigness, yet I'm sure most of the missing data is dependent on league–with lesser known leagues having more missing data, thereby making it Missing at Random(MAR). Pick information is missing for player rows yet present for team rows–but it seems to be Missing by Design(MD) since none of the player rows have pick information. 

## Missingness Dependency

**Missingness of 'ban1' is dependent on 'league'**

In [243]:
def tvd(dist1, dist2):
    return np.abs(dist1 - dist2).sum() / 2


In [296]:
sub = lol[['ban1', 'league']]
dist = sub.assign(ban1_missing = sub['ban1'].isna()).pivot_table(index = 'league', columns = 'ban1_missing', aggfunc='size')

dist = dist.fillna(0)

dist = dist/ dist.sum()

observed_tvd = tvd(dist[False], dist[True])

tvds = []
for _ in range(1000):
    shuffled = sub.assign(league = np.random.permutation(sub['league']))
    dist_shuffled = shuffled.assign(ban1_missing = shuffled['ban1'].isna()).pivot_table(index = 'league', columns = 'ban1_missing', aggfunc='size')
    dist_shuffled = dist_shuffled.fillna(0)
    dist_shuffled = dist_shuffled/ dist_shuffled.sum()
    tvds.append(tvd(dist_shuffled[False], dist_shuffled[True]))





In [297]:
p_val_miss = [tvds]
fig = px.histogram(pd.DataFrame(tvds), histnorm='probability', nbins = 5)
fig.add_vline(observed_tvd, line_color = 'red', line_width = 3)
fig.update_layout(xaxis_title = 'TVD', yaxis_title = 'probability', title = 'Distribution of TVDs')

fig.update_xaxes(range = [0, 1])
fig.show()

In [17]:
lol['league']

0

In [322]:
sub = lol[['side', 'ban1']]
dist = sub.assign(ban1_missing = sub['ban1'].isna()).pivot_table(index = 'side', columns = 'ban1_missing', aggfunc='size')
dist = dist/ dist.sum()
observed_tvd = tvd(dist[False], dist[True])

tvds_2 = []
for _ in range(1000):
    shuffled = sub.assign(side = np.random.permutation(sub['side']))
    dist_shuffled = shuffled.assign(ban1_missing = shuffled['ban1'].isna()).pivot_table(index = 'side', columns = 'ban1_missing', aggfunc='size')
    dist_shuffled = dist_shuffled.fillna(0)
    dist_shuffled = dist_shuffled/ dist_shuffled.sum()
    tvds_2.append(tvd(dist_shuffled[False], dist_shuffled[True]))



In [323]:

fig = px.histogram(pd.DataFrame(tvds_2), histnorm='probability')
fig.add_vline(observed_tvd, line_color = 'red', line_width = 3)
fig.update_layout(xaxis_title = 'TVD', yaxis_title = 'probability', title = 'Distribution of TVDs')
fig.update_xaxes(range = [0, 0.1])
fig.show()

## Step 4: Hypothesis Testing

In [327]:
mean_blue_wr = pick_df[pick_df['side'] == 'Blue']['result'].mean()


observed_won = pick_df[(pick_df['side'] == 'Blue') & (pick_df['pick5'] == 'Renekton')]['result'].sum()



sims = np.random.multinomial(215, [mean_blue_wr, 1-mean_blue_wr], 10000)
num_won = sims[:, 0]

p_val = np.count_nonzero(num_won <= observed_won) / 10000

significance = 0.05

fig = px.histogram(num_won)
fig.add_vline(x = observed_won, line_color =  'red', line_width = 3)
fig.update_layout(xaxis_title = 'wins', title = 'Empirical Distribution for Blue Side Winrate')
fig.show()


In [225]:



roles = ['top', 'jg', 'adc', 'mid', 'sup']

for role in roles:
    perm_test = []
    smaller_df = ban_counts[[role, 'result']]
    observed_diff = abs(average_bans_by_result.loc[1, role] - average_bans_by_result.loc[0, role])

    for i in range(1000):
        shuffled = smaller_df.assign(result = np.random.permutation(smaller_df['result']))
        abs_expected_diff = abs(shuffled.groupby('result').mean().loc[0] - shuffled.groupby('result').mean().loc[1])
        perm_test.append(abs_expected_diff)
    
    p_val = np.mean([observed_diff <= i for i in perm_test])
    print(f'{role}, p-value:{p_val}')

    fig = px.histogram(perm_test, title=f'Permutation Test: {role.capitalize()}')
    fig.add_vline(x = observed_diff, line_color =  'red', line_width = 3)
    
    fig.update_layout(xaxis_title="Permuted Differences", yaxis_title="Frequency")
    
    fig.show()
    

    
    

top, p-value:0.0074


jg, p-value:0.0


adc, p-value:0.0011


mid, p-value:0.4882


sup, p-value:0.2233


## Step 5: Framing a Prediction Problem

We're going to be predicting the result of a game based on pick-ban information. This is a classification problem, and the response variable is going to be the "result" column–0 represents a loss and 1 represents a win. We'll evaluate the models performance using accuracy, since wins and losses are balanced in our dataset and we're interested in the overall performance of our model.

## Step 6: Baseline Model

In [88]:
from sklearn.compose import ColumnTransformer
from sklearn.decomposition import TruncatedSVD
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline, make_pipeline
from sklearn.preprocessing import OneHotEncoder


def mca(X_train, X_test, n_components=600):
    encoder = OneHotEncoder(sparse=False, handle_unknown='ignore')
    X_train_encoded = encoder.fit_transform(X_train)
    X_test_encoded = encoder.transform(X_test)
    X_train_centered = X_train_encoded - X_train_encoded.mean(axis=0)
    X_test_centered = X_test_encoded - X_train_encoded.mean(axis=0)  
    svd = TruncatedSVD(n_components=n_components)
    svd.fit(X_train_centered)
    transformed_X_train = svd.transform(X_train_centered)
    transformed_X_test = svd.transform(X_test_centered)
    
    return transformed_X_train, transformed_X_test

y = pick_df['result']
X = pick_df[['pick1', 'pick2', 'pick3', 'pick4', 'pick5', 'side', 'patch', 'ban1', 'ban2', 'ban3', 'ban4', 'ban5']]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)
transformed_X_train, transformed_X_test = mca(X_train, X_test, n_components=500)



In [39]:
rf = RandomForestClassifier(n_estimators=100, max_depth=30)
rf.fit(transformed_X_train, y_train)

rf.score(transformed_X_test, y_test)

0.5096918489065606

In [51]:
from sklearn.linear_model import LogisticRegression


lr = LogisticRegression(C=0.01, solver='liblinear', intercept_scaling=10)
lr.fit(transformed_X_train, y_train)
lr.score(transformed_X_test, y_test)


0.5350397614314115

In [58]:
from sklearn.neural_network import MLPClassifier


mlp = MLPClassifier()
mlp.fit(transformed_X_train, y_train)
mlp.score(transformed_X_test, y_test)



0.5211232604373758

In [90]:
from sklearn import svm


nb = svm.SVC()
nb.fit(transformed_X_train, y_train)
nb.score(transformed_X_test, y_test)


0.5372763419483101

In [ ]:
0.5559145129224652

In [89]:
from sklearn.neighbors import KNeighborsClassifier


knn = KNeighborsClassifier(n_neighbors= 120,  weights = 'distance', metric = 'euclidean')
knn.fit(transformed_X_train, y_train)
knn.score(transformed_X_test, y_test)




0.532803180914513

manual mca since sci-kit learn doesn't support it. 

In [25]:
pick_df.to_csv('newpicks.csv')

In [437]:
pick_df.columns

Index(['gameid', 'side', 'ban1', 'ban2', 'ban3', 'ban4', 'ban5', 'pick1',
       'pick2', 'pick3', 'pick4', 'pick5', 'league', 'patch', 'result',
       'ban1_pos', 'ban2_pos', 'ban3_pos', 'ban4_pos', 'ban5_pos', 'pick1_pos',
       'pick2_pos', 'pick3_pos', 'pick4_pos', 'pick5_pos'],
      dtype='object')

## Step 7: Final Model

gameid  side      ban1     ban2  ... pick2_pos  \
0           8401-8401_game_1  Blue  Renekton  Lee Sin  ...        jg   
1           8401-8401_game_1   Red    Samira    Diana  ...       sup   
2           8401-8401_game_2  Blue  Renekton  Caitlyn  ...       adc   
...                      ...   ...       ...      ...  ...       ...   
23343  ESPORTSTMNT06_2580514   Red     Galio  Trundle  ...        jg   
23344  ESPORTSTMNT06_2580527  Blue      Azir  Karthus  ...       sup   
23345  ESPORTSTMNT06_2580527   Red     Galio  Trundle  ...       adc   

      pick3_pos pick4_pos pick5_pos  
0           sup       mid       top  
1           adc       mid       top  
2           sup       top       mid  
...         ...       ...       ...  
23343       sup       mid       top  
23344       mid        jg       top  
23345       sup       mid       top  

[20120 rows x 25 columns]

## Step 8: Fairness Analysis

In [ ]:
# TODO